In [1]:
from __future__ import print_function, division

import torch
import torch.nn as nn
import torch.optim as optim
from torch.optim import lr_scheduler
import torch.backends.cudnn as cudnn
import numpy as np
import torchvision
from torchvision import datasets, models, transforms
import time
import os
import copy
from glob import glob
import pandas as pd
from PIL import Image
import torchdata.datapipes as dp
import random
from torch.utils.data.backward_compatibility import worker_init_fn
from sklearn.metrics import classification_report
# import wandb
# import plotly.graph_objects as go
import plotly.express as px
import matplotlib.pyplot as plt
from sklearn.manifold import TSNE

In [2]:
resize_image_size = 1024
data_transforms = {
    'train': transforms.Compose([
        transforms.RandomResizedCrop(resize_image_size),
        transforms.ToTensor(),
        transforms.Normalize(mean=[0.485, 0.456, 0.406],
                             std=[0.229, 0.224, 0.225])
    ]),
    'val': transforms.Compose([
        transforms.Resize(resize_image_size),
        transforms.ToTensor(),
        transforms.Normalize(mean=[0.485, 0.456, 0.406],
                             std=[0.229, 0.224, 0.225])
    ]),
    'test': transforms.Compose([
        transforms.Resize(resize_image_size),
        transforms.ToTensor(),
        transforms.Normalize(mean=[0.485, 0.456, 0.406],
                             std=[0.229, 0.224, 0.225])
    ]),
}

In [3]:
def open_image(inputs):
    wsi_name, img_path, label = inputs
    img = Image.open(img_path)
    return wsi_name, img, int(label)

def apply_train_transforms(inputs):
    wsi_name, x, y = inputs
    return wsi_name, data_transforms["train"](x), y

def apply_val_transforms(inputs):
    wsi_name, x, y = inputs
    return wsi_name, data_transforms["val"](x), y

def build_data_pipe(csv_file, transform , batch_size=32):
    new_dp = dp.iter.FileOpener([csv_file])
    new_dp = new_dp.parse_csv(skip_lines=1)
    # returns tuples like ('0','filename', 'filepath', 'label')
    if transform == "train":
        new_dp = new_dp.shuffle()
    
    new_dp = new_dp.sharding_filter()
    # important to use sharding_filter after (not before) shuffling -For the data source that needs to be sharded, it is crucial to add Shuffler before ShardingFilter to ensure data are globally shuffled before being split into shards. Otherwise, each worker process would always process the same shard of data for all epochs. And, it means each batch would only consist of data from the same shard, which leads to low accuracy during training. However, it doesn’t apply to the data source that has already been sharded for each multi-/distributed process, since ShardingFilter is no longer required to be presented in the pipeline.

    new_dp = new_dp.map(open_image)

    if transform == "train":
        new_dp = new_dp.map(apply_train_transforms)
        new_dp = new_dp.batch(batch_size=batch_size, drop_last=True)

    elif transform == "val":
        new_dp = new_dp.map(apply_val_transforms)
        new_dp = new_dp.batch(batch_size=batch_size, drop_last=False)

    else:
        raise ValueError("Invalid transform argument.")

    new_dp = new_dp.map(torch.utils.data.default_collate)
    return new_dp

In [4]:
# data  = pd.read_csv("/gladstone/finkbeiner/steve//work/data/npsad_data/vivek/Datasets/amyb_wsi/apoe_training_dataset/data_with_detection.csv")

batch_size = 6
# data = data[["Imaging_XENum","crop_filepath","apoe_label"]]

# data.to_csv("/gladstone/finkbeiner/steve//work/data/npsad_data/vivek/Datasets/amyb_wsi/apoe_training_dataset/data_with_detection_less_feature.csv")
TRAIN_CSV = "/mnt/new-nas/work/data/npsad_data/vivek/Datasets/amyb_wsi/apoe_training_dataset/train_detected_full2.csv"
data  = pd.read_csv(TRAIN_CSV)
data = data[["Imaging_XENum","crop_filepath","apoe_label"]]
data.to_csv("/mnt/new-nas/work/data/npsad_data/vivek/Datasets/amyb_wsi/apoe_training_dataset/train_detected_full2_less_feature.csv")


In [5]:
def dataset_size(csv_file):
    df = pd.read_csv(csv_file)
    return len(df)

train_datasize = dataset_size(TRAIN_CSV)
dataset_sizes = {'train':train_datasize}

In [6]:
train_dp = build_data_pipe(TRAIN_CSV, "train", batch_size)

In [7]:
train_loader = torch.utils.data.DataLoader(
    dataset=train_dp, shuffle=True, num_workers=4)


dataloaders = {"train":train_loader}

device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

In [8]:
def load_saved_model(path):
    checkpoint = torch.load(path)
    model_ft = checkpoint["model"]
    model_ft.load_state_dict(checkpoint['state'])
    return model_ft

path = '/mnt/new-nas/work/data/npsad_data/monika/Amy_plaque_Results/models/model_squished_label_detected.pth'
model_ft = load_saved_model(path)
model_ft = model_ft.to(device)

In [9]:
#model_ft = models.resnet18(pretrained=True)
model_ft.fc_backup = model_ft.fc
model_ft.fc = nn.Sequential()


In [10]:
next(iter(dataloaders['train']))


ValueError: Caught ValueError in DataLoader worker process 0.
Original Traceback (most recent call last):
  File "/home/vivek/.virtualenvs/mask_rcnn-w0kK5vJa/lib/python3.8/site-packages/torch/utils/data/_utils/worker.py", line 308, in _worker_loop
    data = fetcher.fetch(index)
  File "/home/vivek/.virtualenvs/mask_rcnn-w0kK5vJa/lib/python3.8/site-packages/torch/utils/data/_utils/fetch.py", line 32, in fetch
    data.append(next(self.dataset_iter))
  File "/home/vivek/.virtualenvs/mask_rcnn-w0kK5vJa/lib/python3.8/site-packages/torch/utils/data/datapipes/_hook_iterator.py", line 144, in __next__
    return self._get_next()
  File "/home/vivek/.virtualenvs/mask_rcnn-w0kK5vJa/lib/python3.8/site-packages/torch/utils/data/datapipes/_hook_iterator.py", line 132, in _get_next
    result = next(self.iterator)
  File "/home/vivek/.virtualenvs/mask_rcnn-w0kK5vJa/lib/python3.8/site-packages/torch/utils/data/datapipes/_hook_iterator.py", line 215, in wrap_next
    result = next_func(*args, **kwar

In [ ]:
actual_labels = []
wsi_names = []
feature_list=[]
for i, (wsi, inputs, labels) in enumerate(dataloaders['train']):
    inputs=inputs.squeeze()
    labels = labels.squeeze()
    inputs = inputs.to(device)
    labels = labels.to(device)
    features = model_ft(inputs)
    feature_list.extend(features.cpu().tolist())
    actual_labels.extend(labels.tolist())
    wsi=[x[0] for x in wsi]
    wsi_names.extend(wsi)
    

ValueError: Caught ValueError in DataLoader worker process 0.
Original Traceback (most recent call last):
  File "/home/vivek/.virtualenvs/mask_rcnn-w0kK5vJa/lib/python3.8/site-packages/torch/utils/data/_utils/worker.py", line 308, in _worker_loop
    data = fetcher.fetch(index)
  File "/home/vivek/.virtualenvs/mask_rcnn-w0kK5vJa/lib/python3.8/site-packages/torch/utils/data/_utils/fetch.py", line 32, in fetch
    data.append(next(self.dataset_iter))
  File "/home/vivek/.virtualenvs/mask_rcnn-w0kK5vJa/lib/python3.8/site-packages/torch/utils/data/datapipes/_hook_iterator.py", line 144, in __next__
    return self._get_next()
  File "/home/vivek/.virtualenvs/mask_rcnn-w0kK5vJa/lib/python3.8/site-packages/torch/utils/data/datapipes/_hook_iterator.py", line 132, in _get_next
    result = next(self.iterator)
  File "/home/vivek/.virtualenvs/mask_rcnn-w0kK5vJa/lib/python3.8/site-packages/torch/utils/data/datapipes/_hook_iterator.py", line 215, in wrap_next
    result = next_func(*args, **kwar

In [ ]:
len(feature_list)

0

In [ ]:
feature_list

[]

In [ ]:
tsne_model = TSNE(n_components=2, random_state=0, learning_rate='auto', init='random', perplexity=50)

In [ ]:
projections = tsne_model.fit_transform(np.array(feature_list))

UFuncTypeError: ufunc 'multiply' did not contain a loop with signature matching types (dtype('<U32'), dtype('<U32')) -> dtype('<U32')

In [ ]:
tsne_data = np.vstack((projections.T, actual_labels)).T
tsne_df = pd.DataFrame(data=tsne_data, columns=("Dim_1", "Dim_2", "label"))

NameError: name 'projections' is not defined

In [ ]:
tsne_df

Dim_1      Dim_2  label
0      20.456902  18.668934    1.0
1      10.640992 -46.471916    1.0
2      30.307983  29.263294    0.0
3      13.050817  57.311951    2.0
4      -2.620098 -65.009430    2.0
...          ...        ...    ...
13339  57.294735  23.582644    0.0
13340 -24.526297   1.388282    0.0
13341 -15.358237 -36.331181    1.0
13342  -7.264002  61.243721    1.0
13343   0.749488 -64.422432    1.0

[13344 rows x 3 columns]

In [ ]:

fig = px.scatter(
    projections, x=0, y=1,
    color=tsne_df.label, labels={'color': 'label'}
)
fig.show()

In [ ]:

fig = px.scatter(
    projections, x=0, y=1,
    color=tsne_df.label, labels={'color': 'label'}
)
fig.show()

In [ ]:
dinov2_vitl14 = torch.hub.load('facebookresearch/dinov2', 'dinov2_vits14')
#dinov2_vitl14=dinov2_vitl14.to(device)

Using cache found in /home/mahirwar/.cache/torch/hub/facebookresearch_dinov2_main
xFormers not available
xFormers not available


In [ ]:
#dinov2_vitl14 = dinov2_vitl14.to(device)

In [ ]:
# image size should be a multiple of 14
actual_labels = []
wsi_names = []
feature_list=[]
for i, (wsi, inputs, labels) in enumerate(dataloaders['train']):
    print(i)
    inputs=inputs.squeeze(0)
    labels = labels.squeeze(0)
    #inputs = inputs.to(device)
    #labels = labels.to(device)
    #features = model_ft(inputs)
    image_features = dinov2_vitl14(inputs)
    #features = model_ft(inputs)
    feature_list.extend(image_features.cpu().tolist())
    actual_labels.extend(labels.tolist())
    wsi=[x[0] for x in wsi]
    wsi_names.extend(wsi)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

In [ ]:
wsi_names

['XE12-015', 'XE14-047', 'XE14-047', 'XE15-007']

In [ ]:
image_features.shape

torch.Size([2, 384])

In [ ]:
len(image_features.cpu().tolist())

2

In [ ]:
imf = image_features.cpu().tolist()

In [ ]:
len(imf[1])

384

In [ ]:
labels.tolist()

[1, 2]

In [ ]:
actual_labels

[1, 1, 0, 2]

In [ ]:
len(feature_list)

4

In [ ]:
wsi

['XE15-007', 'XE12-015']

In [ ]:
len(image_features.cpu().tolist())

2

In [ ]:
len(feature_list)

2

In [ ]:
len(feature_list[1][1])

384

In [ ]:
len(feature_list[0])

384

In [ ]:
len(feature_list[0])

384

In [ ]:
tsne_model = TSNE(n_components=2, random_state=0, learning_rate='auto', init='random', perplexity=50)
projections = tsne_model.fit_transform(np.array(feature_list))
tsne_data = np.vstack((projections.T, actual_labels)).T
tsne_df = pd.DataFrame(data=tsne_data, columns=("Dim_1", "Dim_2", "label"))

fig = px.scatter(
    projections, x=0, y=1,
    color=tsne_df.label, labels={'color': 'label'}
)
fig.show()